# setup

## import stuff

In [ ]:
# regulary used
from copy import deepcopy
from IPython.display import IFrame
import json
import matplotlib
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import axes3d
from mpl_toolkits.axes_grid1 import make_axes_locatable
import numpy as np
import os
import pandas as pd
import pickle
import tempfile
import scipy
from scipy import constants as const
from scipy import integrate
from scipy import optimize

# available on https://github.com/marvinbernhardt/gromacstools
import gromacstools as gt
run_bash = gt.general.run_bash
WorkingDir = gt.general.WorkingDir

# own constants
const.k_gro = const.k * const.N_A * 1e-3
const.h_gro = const.h * const.N_A * 1e-3 * 1e12
const.hbar_gro = const.hbar * const.N_A * 1e-3 * 1e12
const.rec_cm_per_THz = 1e12 / const.c / 100

# notebook wide variables
jobids = []

## notebook specific constants/settings

In [ ]:
project_label = "21-tennis-racket-critical"
template_dir = os.path.join(os.getcwd(), 'template')
plt.style.use('seaborn-muted')
!mkdir -p figures

## remote computing resource

In [ ]:
#defines some variables related to the slurm HPC clusters used for the expensive computations

remote_host = "franklin"
remote_dir_base = os.path.join("/home/mbernhardt/run", project_label)
remote_footer = ''

In [ ]:
remote_header = """#!/bin/sh
#SBATCH --job-name=md
#SBATCH --exclusive
#SBATCH --time=4:00:00
#SBATCH --partition=enzo

set -euo pipefail
shopt -s expand_aliases
module purge
# netlib-lapack@3.8.0
spack load /dthwmyc
#fftw@3.3.8~mpi~openmp~pfft_patches precision=double,float
spack load /e4wa6u5
alias dos-calc="/home/mbernhardt/bin/dos-calc"
# gromacs@2019.5 build_type=RelWithDebInfo ~cuda~double~double_precision+hwloc~mdrun_only~mpi+openmp~plumed+rdtscp+shared simd=SSE2
spack load /6wmvagj 
alias gmx="gmx -quiet"
"""

In [ ]:
remote_header = """#!/bin/sh
#SBATCH --job-name=md
#SBATCH --ntasks=10
#SBATCH --time=4:00:00
#SBATCH --partition=enzogpu

set -euo pipefail
shopt -s expand_aliases
module purge
# netlib-lapack@3.8.0
spack load /dthwmyc
#fftw@3.3.8~mpi~openmp~pfft_patches precision=double,float
spack load /e4wa6u5
alias dos-calc="/home/mbernhardt/bin/dos-calc"
# gromacs@2019 build_type=RelWithDebInfo +cuda~double~mpi~plumed+rdtscp+shared simd=AVX2_256
spack load /yfcl45y
alias gmx="gmx -quiet"
"""

In [ ]:
remote_header = """#!/bin/sh
#SBATCH --job-name=md
#SBATCH --exclusive
#SBATCH --time=4:00:00
#SBATCH --partition=biby
#SBATCH --account=ccteam

set -euo pipefail
shopt -s expand_aliases
module purge
# netlib-lapack@3.8.0
spack load /dthwmyc
# fftw@3.3.8~mpi~openmp~pfft_patches precision=double,float
spack load /e4wa6u5
alias dos-calc="/home/mbernhardt/bin/dos-calc"
# gromacs@2019.3 build_type=RelWithDebInfo ~cuda~double~mpi~plumed~rdtscp+shared simd=SSE2
spack load /rf37djz
alias gmx="gmx -quiet"
"""

In [ ]:
#defines some variables related to the slurm HPC clusters used for the expensive computations

remote_host = "sniffa"
remote_dir_base = os.path.join("/home/mbernhardt/run", project_label)
remote_footer = "rm -rf $JOBTMP"

In [ ]:
remote_header = """#!/bin/sh
#SBATCH --job-name=md
#SBATCH --nodes=1
#SBATCH --ntasks=1
#SBATCH --cpus-per-task=12
#SBATCH --time=4:00:00
#SBATCH --partition=batch
#SBATCH --exclude=node[03,05-08]

JOBTMP="/tmp/$(mktemp -u data${SLURM_JOB_ID}XXXXXXXXXXXXXX)"
mkdir -p $JOBTMP

module purge
module load gcc/8.2.0

export SPACK_ROOT=/shared/spack
. $SPACK_ROOT/share/spack/setup-env.sh

set -euo pipefail
shopt -s expand_aliases
# netlib-lapack@3.8.0
spack load /c5uo7hy
spack load fftw
spack load gromacs
alias gmx="gmx -quiet"
alias dos-calc="/home/mbernhardt/bin/dos-calc"
"""

## DoS parameters

In [ ]:
dos_names = [
    {'name': 'trn', 'tags': [], 'ndof': 3},
    {'name': 'rot', 'tags': [], 'ndof': 3},
    {'name': 'vib', 'tags': [], 'ndof': None},
    {'name': 'roto_a', 'tags': ['comp'], 'ndof': 1},
    {'name': 'roto_b', 'tags': ['comp'], 'ndof': 1},
    {'name': 'roto_c', 'tags': ['comp'], 'ndof': 1},
]

param_dos = {
    'n_samples': 5,
    'n_blocks': 10,
    'n_frames_per_block': 1000,
}

## systems

In [ ]:
# some helper functions for system generation

def gen_states(properties, rho_grid, T_grid):
    rho_min, rho_max, rho_num = rho_grid
    T_min, T_max, T_num = T_grid
    densities = np.round(np.linspace(rho_min, rho_max, num=rho_num) * properties['rho_c'], 4)
    temperatures = np.round(np.linspace(T_min, T_max, num=T_num) * properties['T_c'], 0)
    states = [{'rho': rho, 'T': T} for rho in densities for T in temperatures]
    return states

def calc_if_stable_state(state, properties):
    vap_liq_equi = properties['vap_liq_equi']
    rho_c = properties['rho_c']
    T_c = properties['T_c']
    two_phase_region_x = np.concatenate((np.sort(vap_liq_equi['rho_vap']), [rho_c], np.sort(vap_liq_equi['rho_liq'])))
    two_phase_region_y = np.concatenate((np.sort(vap_liq_equi['T']), [T_c], np.sort(vap_liq_equi['T'])[::-1]))
    if state['T'] > np.interp(state['rho'], two_phase_region_x, two_phase_region_y):
        return True
    else:
        return False

def volume_from_rho_M_N(density, molar_mass, n_mols):
    """
    density in g/mL
    molar_mass in g/mol
    n_mols
    """
    system_mass = n_mols * molar_mass / const.N_A  # in g
    volume = system_mass / density  # in mL
    return volume / 1e-21 # in nm³

def show_phase_diag(system_type, states):
    params = {'text.usetex' : False,
              'font.family': 'serif',
              'axes.labelsize': 10,
              'font.size': 10,
              'legend.fontsize': 8,
              'xtick.labelsize': 8,
              'ytick.labelsize': 8,
              'figure.dpi': 100,
             }
    with plt.rc_context(rc=params):
        fig, ax1 = plt.subplots(figsize=(3,2))
        ax1.set_title(system_type['name'])
        ax1.set_xlabel(r"$\rho$ in g/ml")
        ax1.set_ylabel(r"$T$ in K")
        rho_c = system_type['properties']['rho_c']
        T_c = system_type['properties']['T_c']
        vap_x = np.concatenate((np.sort(system_type['properties']['vap_liq_equi']['rho_vap']), [rho_c]))
        liq_x = np.concatenate((np.sort(system_type['properties']['vap_liq_equi']['rho_liq'])[::-1], [rho_c]))
        y = np.concatenate((np.sort(system_type['properties']['vap_liq_equi']['T']), [T_c]))
        ax1.plot(vap_x, y, label='vapor line')
        ax1.plot(liq_x, y, label='liquid line')
        ax1.plot([state['rho'] for state in states],
                 [state['T'] for state in states],
                 '.', label='states')
        ax1.legend()
        plt.show()

In [ ]:
# for which state to test thermostat
i_test_thermostat = 2
names_test_stiff = ["propane/idgas-478K", "propane/0.0022-478K"]

In [ ]:
atomtypes = {'O': {'name': 'O', 'mass': 15.9994},
             'H': {'name': 'H', 'mass':  1.008},
             'M': {'name': 'M', 'mass':  0.0},
             'He': {'name': 'He', 'mass': 4.0026},
             'CH2': {'name': 'CH2', 'mass': 14.02700},
             'CH3': {'name': 'CH3', 'mass': 15.03500}}

water_atoms = [atomtypes[atom] for atom in ['O', 'H', 'H', 'M']]
water_moltypes = [{'name': "SOL", 'atoms': water_atoms, 'nmols': 2000,
                   'sigma': 2, 'abc_indicators': [1, 2, 0, -1], 'rot_treat': 'f'}]
water_vap_liq_equi = pd.DataFrame({
    'T': [620, 610, 600, 590, 570, 550, 530, 510, 490, 470, 450, 430, 410, 390, 370, 350, 330, 310, 300, 290, 270],
    'rho_liq': [0.561, 0.598, 0.629, 0.650, 0.703, 0.741, 0.775, 0.807, 0.835, 0.861, 0.883, 0.905, 0.923, 0.943, 0.9585, 0.9713, 0.9841, 0.9932, 0.9965, 0.9990, 0.9999],
    'rho_vap': [10.3E-2, 7.44E-2, 5.93E-2, 4.63E-2, 3.16E-2, 2.13E-2, 1.415E-2, 9.35E-3, 6.09E-3, 3.85E-3, 2.342E-3, 1.379E-3, 7.59E-4, 3.966E-4, 1.891E-4, 8.23E-5, 3.166E-5, 1.055E-5, 5.642E-6, 2.900E-6, 6.358E-7],
})
water_properties = {'T_c': 640, 'rho_c': 0.310, 'vap_liq_equi': water_vap_liq_equi}

propane_atoms = [atomtypes[atom] for atom in ['CH2', 'CH3', 'CH3']]
propane_moltypes = [{'name': "PRO", 'atoms': propane_atoms, 'nmols': 2000,
                     'sigma': 2, 'abc_indicators': [1, 2, 0, -1], 'rot_treat': 'f'}]
propane_vap_liq_equi = pd.DataFrame({
    'T': np.array([217, 249, 281, 312, 344])[::-1],
    'rho_liq': np.array([0.598, 0.560, 0.517, 0.467, 0.396])[::-1],
    'rho_vap': np.array([0.0020, 0.0063, 0.018, 0.033, 0.066])[::-1],
})
propane_properties = {'T_c': 368, 'rho_c': 0.221, 'vap_liq_equi': propane_vap_liq_equi}


system_types = [
    {'name': 'water', 'moltypes': water_moltypes, 'properties': water_properties},
    {'name': 'propane', 'moltypes': propane_moltypes, 'properties': propane_properties}
]

for system_type in system_types:
    states_unfiltered = gen_states(system_type['properties'], (0.01, 0.51, 5), (0.55, 2.05, 7))
    states_unfiltered += gen_states(system_type['properties'], (0.71, 3.11, 9), (0.55, 2.05, 7))
    states = [state for state in states_unfiltered if calc_if_stable_state(state, system_type['properties'])]
    system_type['states'] = states
    show_phase_diag(system_type, states)
    

systems = []
for system_type in system_types:
    typename = system_type['name']
    moltypes = system_type['moltypes']
    molstates = system_type['states']
    idgas_temperatures = []
    for i, state in enumerate(molstates):
        if state['T'] not in idgas_temperatures:
            idgas_temperatures.append(state['T'])
        density = state['rho']
        temperature = state['T']
        if i == i_test_thermostat:
            tags = ['test_thermostat']
        else:
            tags = []
        systems.append({'name': f"{typename}/{density:.4f}-{temperature:.0f}K", 'temperature': temperature, 'density': density,
                        'moltypes': deepcopy(moltypes), 'type': typename, 'tags': tags})
    # ideal gas states
    density = max((molstate['rho'] for molstate in molstates))
    for temperature in idgas_temperatures:
        systems.append({'name': f"{typename}/idgas-{temperature:.0f}K", 'temperature': temperature, 'density': density,
                        'moltypes': deepcopy(moltypes), 'type': typename, 'tags': ['idgas']})
    
# some additional fields for later use
for system_nr, system in enumerate(systems):
    top = gt.top.Topology()
    top.load_simple_top(system['moltypes'])
    system['top'] = top
    nmols = system['top'].nmols()
    molar_mass = sum((mol.mass for mol in top.mols())) / nmols
    system['volume'] = volume_from_rho_M_N(system['density'], molar_mass, nmols)
    if system['name'] in names_test_stiff:
        system['tags'].append('test_stiff')
    
# print systems
for system_nr, system in enumerate(systems):
    print(f"{system_nr:2d}  {system['name']:12s}  {system['volume']:.3f}  {system['temperature']}  {system['type']}  {system['tags']}")

In [ ]:
for system_type in system_types:
    print(system_type['name'])
    for state in system_type['states']:
        print(state, end=' ')
        print('rho* = {:.3f}, T* = {:.3f}'.format(
            state['rho'] / system_type['properties']['rho_c'],
            state['T'] / system_type['properties']['T_c']))

## often used helper functions

In [ ]:
def check_job_stati(jobids, remote_host):
    stati = gt.remote.check_slurm_jobs(jobids, remote_host)

    # print status for each job
    completed_jobids = []
    for jobid, status in zip(jobids, stati):
        print(jobid, status)
        if (status in ('FAILED', 'COMPLETED', None)
            or status.startswith('CANCELLED')):
            completed_jobids.append(jobid)

    # remove jobids which are completed
    new_jobids = [jobid for jobid in jobids if jobid not in completed_jobids]
    return new_jobids

## thermostats to test

In [ ]:
# tested thermostats
thermostats_to_test = [
    {'name': 'no', 'key': 'no', 'tau-t': None},
    {'name': 'sd-5', 'key': 'sd', 'tau-t': 5},
    {'name': 'sd-20', 'key': 'sd', 'tau-t': 20},
    {'name': 'sd-80', 'key': 'sd', 'tau-t': 80},
    {'name': 'sd-320', 'key': 'sd', 'tau-t': 320},
    {'name': 'v-rescale-0.5', 'key': 'v-rescale', 'tau-t': 0.5},
    {'name': 'v-rescale-2', 'key': 'v-rescale', 'tau-t': 2},
    {'name': 'v-rescale-8', 'key': 'v-rescale', 'tau-t': 8},
    {'name': 'v-rescale-32', 'key': 'v-rescale', 'tau-t': 32},
    {'name': 'andersen-massive-2', 'key': 'andersen-massive', 'tau-t': 2},
    {'name': 'andersen-massive-10', 'key': 'andersen-massive', 'tau-t': 10},
    {'name': 'andersen-massive-40', 'key': 'andersen-massive', 'tau-t': 40},
    {'name': 'andersen-massive-160', 'key': 'andersen-massive', 'tau-t': 160},
]

# data generation

## prepare MD simulations

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    box_edge = system['volume']**(1/3)
          
    with WorkingDir(system['name']):
        # make dirs and copy template files
        run_bash("mkdir -p equi1 equi2 prod topol")
        system_type = system['type']
        if 'idgas' in system['tags']:
            run_bash(f"cp -Tr {template_dir}/{system_type}/idgas/topol topol")
            run_bash(f"cp {template_dir}/{system_type}/idgas/equi1.mdp equi1/grompp.mdp")
            run_bash(f"cp {template_dir}/{system_type}/idgas/equi2.mdp equi2/grompp.mdp")
            run_bash(f"cp {template_dir}/{system_type}/idgas/prod.mdp prod/grompp.mdp")
        else:
            run_bash(f"cp -Tr {template_dir}/{system_type}/topol topol")
            run_bash(f"cp {template_dir}/{system_type}/equi1.mdp equi1/grompp.mdp")
            run_bash(f"cp {template_dir}/{system_type}/equi2.mdp equi2/grompp.mdp")
            run_bash(f"cp {template_dir}/{system_type}/prod.mdp prod/grompp.mdp")
        run_bash(f"cp {template_dir}/{system_type}/single-* .")

        # run length
        gt.mdp.set_parameter("equi1/grompp.mdp", 'nsteps',  10000)
        gt.mdp.set_parameter("equi2/grompp.mdp", 'nsteps', 400000)
        gt.mdp.set_parameter("prod/grompp.mdp", 'nsteps',  800000)
        
        # set temperature
        if 'idgas' in system['tags']:
            gt.mdp.set_parameter("equi1/grompp.mdp", 'gen-temp', system['temperature'])
            gt.mdp.set_parameter("equi1/grompp.mdp", 'ref-t', system['temperature'])
        else:
            gt.mdp.set_parameter("equi2/grompp.mdp", 'gen-temp', system['temperature'])
        gt.mdp.set_parameter("equi2/grompp.mdp", 'ref-t', system['temperature'])
        gt.mdp.set_parameter("prod/grompp.mdp", 'ref-t',  system['temperature'])

## prepare DoS calculation

In [ ]:
for system in systems:
    print(f"system {system['name']}")
          
    with WorkingDir(system['name']):
        run_bash("mkdir -p dos")
        top = system['top']
        params = {
'nsamples': param_dos['n_samples'],
'nblocks': param_dos['n_blocks'],
'nblocksteps': param_dos['n_frames_per_block'],
'moltypes': [{
    'nmols': moltype['nmols'],
    'atom_masses': [atom['mass'] for atom in moltype['atoms']],
    'rot_treat': moltype['rot_treat'],
    'abc_indicators': moltype['abc_indicators']
} for moltype in system['moltypes']],
'cross_spectra': []
}
        
        with open('dos/params.json', 'w') as f:
            json.dump(params, f, indent=4)

## fill box

In [ ]:
for system in systems:
    print(f"system {system['name']}")
          
    with WorkingDir(system['name']):
        if not os.path.isfile("equi1/conf.gro"):
            box_edge = system['volume']**(1/3)

            # empty gro file
            empty_gro = f"""system
0
  {box_edge} {box_edge} {box_edge}
    """
            with open("equi1/conf.gro", 'w') as f:
                f.write(empty_gro)

            # insert molecules
            for moltype in system['moltypes']:
                n_mols = moltype['nmols']
                mt_name = moltype['name']
                run_bash(f"gmx insert-molecules -scale 0.7 -f equi1/conf.gro -o equi1/conf.gro -ci single-{mt_name}.gro -nmol {n_mols} -try 100")
                run_bash("rm -f equi1/\#conf.gro.*")

        # check
        n_atoms_inserted = gt.gro.get_natoms("equi1/conf.gro")
        n_atoms_wanted = system['top'].natoms()
        if n_atoms_inserted != n_atoms_wanted:
            print(n_atoms_inserted, n_atoms_wanted)
            raise Exception("not enough molecules inserted")

## MD on cluster

In [ ]:
for system in systems:
    print(f"system {system['name']}")
    remote_dir = os.path.join(remote_dir_base, system['name'])
    
    #if system['type'] == 'water' and system['density'] < 0.16:
        #continue
    #if system['type'] == 'propane' and system['density'] < 0.12:
        #continue
    
    with WorkingDir(system['name']):
        # mkdir
        run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")

        # copy simulation files to remote
        filelist = ["topol",
                    "equi1/conf.gro",
                    "equi1/grompp.mdp",
                    "equi2/grompp.mdp",
                    "prod/grompp.mdp",
                    "dos/params.json"]
        gt.remote.push_files(filelist, remote_host, remote_dir, exclude="traj*")

        # commands to be run on compute nodes
        temperature = system['temperature']
        script = remote_header + f"""
pushd equi1
    if [[ ! -f confout.gro ]]
    then
        gmx grompp -p ../topol/topol.top
        gmx mdrun -nt $SLURM_JOB_CPUS_PER_NODE
    fi
    rm -f \#*
popd

pushd equi2
    if [[ ! -f confout.gro ]]
    then
        gmx grompp -p ../topol/topol.top -c ../equi1/confout.gro
        gmx mdrun -nt $SLURM_JOB_CPUS_PER_NODE
    fi
    rm -f \#*
popd

if [[ ! -f dos/dos.json ]]
then
    pushd prod
        gmx grompp -p ../topol/topol.top -c ../equi2/confout.gro
        gmx mdrun -nt $SLURM_JOB_CPUS_PER_NODE -o $JOBTMP/traj.trr
        ls -lh $JOBTMP/
        rm -f \#*
    popd

    pushd dos
        OMP_NUM_THREADS=$SLURM_JOB_CPUS_PER_NODE dos-calc -vs 1 params.json $JOBTMP/traj.trr
        rm -f \#*
    popd
fi
""" + remote_footer

        jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir, dry_run=False)
        print(jobid)
        if jobid != None:
            jobids.append(jobid)

## check job status

In [ ]:
jobids = check_job_stati(jobids, remote_host)

## fetch results

In [ ]:
# fetch energy files, DoS files and configuration files
filelist = ["**/*.edr", "**/dos.json", "**/*.gro"]
#filelist = ["**/dos.json"]
exclude = "traj*"
gt.remote.pull_files(filelist, remote_host, remote_dir_base, exclude=exclude)

## equilibration check

In [ ]:
def show_energy_graphs(properties_list, edr_file="ener.edr"):
    run_bash("gmx energy -f {} -o energy-temp.xvg <<< '{}'".format(edr_file, "\n".join(properties_list)))
    gt.xvg.plot("energy-temp.xvg")
    run_bash("rm energy-temp.xvg")

In [ ]:
for system in systems:
    print(f"system {system['name']}")
          
    with WorkingDir(system['name']):
        #print("equilibration 1")
        #show_energy_graphs(["Temperature"], edr_file="equi1/ener.edr")
        #show_energy_graphs(["Pressure"], edr_file="equi1/ener.edr")
        #print("equilibration 2")
        #show_energy_graphs(["Temperature"], edr_file="equi2/ener.edr")
        #show_energy_graphs(["Pressure"], edr_file="equi2/ener.edr")
        print("production")
        #show_energy_graphs(["Temperature"], edr_file="prod/ener.edr")
        show_energy_graphs(["Pressure"], edr_file="prod/ener.edr")

# stiff test data generation

## prepare stiff test

In [ ]:
for system in (system for system in systems if 'test_stiff' in system['tags']):
    print(f"system {system['name']}")
          
    with WorkingDir(system['name'] + '-test-stiff'):
        # make dirs and copy template files
        run_bash("mkdir -p equi1 equi2 prod topol dos")
        system_type = system['type']
        if 'idgas' in system['tags']:
            run_bash(f"cp -Tr {template_dir}/{system_type}/idgas/topol-stiff topol")
            run_bash(f"cp {template_dir}/{system_type}/idgas/equi1.mdp equi1/grompp.mdp")
            run_bash(f"cp {template_dir}/{system_type}/idgas/equi2.mdp equi2/grompp.mdp")
            run_bash(f"cp {template_dir}/{system_type}/idgas/prod.mdp prod/grompp.mdp")
        else:
            run_bash(f"cp -Tr {template_dir}/{system_type}/topol-stiff topol")
            run_bash(f"cp {template_dir}/{system_type}/equi1.mdp equi1/grompp.mdp")
            run_bash(f"cp {template_dir}/{system_type}/equi2.mdp equi2/grompp.mdp")
            run_bash(f"cp {template_dir}/{system_type}/prod.mdp prod/grompp.mdp")

        # run length
        gt.mdp.set_parameter("equi1/grompp.mdp", 'nsteps',  10000)
        gt.mdp.set_parameter("equi2/grompp.mdp", 'nsteps', 400000)
        gt.mdp.set_parameter("prod/grompp.mdp", 'nsteps',  800000)
        
        # set temperature
        if 'idgas' in system['tags']:
            gt.mdp.set_parameter("equi1/grompp.mdp", 'gen-temp', system['temperature'])
            gt.mdp.set_parameter("equi1/grompp.mdp", 'ref-t', system['temperature'])
        else:
            gt.mdp.set_parameter("equi2/grompp.mdp", 'gen-temp', system['temperature'])
        gt.mdp.set_parameter("equi2/grompp.mdp", 'ref-t', system['temperature'])
        gt.mdp.set_parameter("prod/grompp.mdp", 'ref-t',  system['temperature'])
        
        # copy dos-params
        run_bash(f"cp ../../{system['name']}/dos/params.json dos/params.json")

        # copy conf.gro
        run_bash(f"cp ../../{system['name']}/equi1/conf.gro equi1/conf.gro")

## stiff test md on cluster

In [ ]:
for system in (system for system in systems if 'test_stiff' in system['tags']):
    print(f"system {system['name']}")
    
    remote_dir = os.path.join(remote_dir_base, system['name'] + '-test-stiff')
    with WorkingDir(system['name'] + '-test-stiff'):

        # mkdir
        run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")

        # copy simulation files to remote
        filelist = ["topol",
                    "equi1/conf.gro",
                    "equi1/grompp.mdp",
                    "equi2/grompp.mdp",
                    "prod/grompp.mdp",
                    "dos/params.json"]
        gt.remote.push_files(filelist, remote_host, remote_dir, exclude="traj*")

        # commands to be run on compute nodes
        temperature = system['temperature']
        script = remote_header + f"""
pushd equi1
    if [[ ! -f confout.gro ]]
        then
        gmx grompp -p ../topol/topol.top
        gmx mdrun -nt $SLURM_JOB_CPUS_PER_NODE
    fi
    rm -f \#*
popd

pushd equi2
    if [[ ! -f confout.gro ]]
    then
        gmx grompp -p ../topol/topol.top -c ../equi1/confout.gro -maxwarn 1
        gmx mdrun -nt $SLURM_JOB_CPUS_PER_NODE
    fi
    rm -f \#*
popd

if [[ ! -f dos/dos.json ]]
then
    pushd prod
        gmx grompp -p ../topol/topol.top -c ../equi2/confout.gro -maxwarn 1
        gmx mdrun -nt $SLURM_JOB_CPUS_PER_NODE -o $JOBTMP/traj.trr
        ls -lh $JOBTMP/
        rm -f \#*
    popd

    pushd dos
        OMP_NUM_THREADS=$SLURM_JOB_CPUS_PER_NODE dos-calc -vs 1 params.json $JOBTMP/traj.trr
        rm -f \#*
    popd
fi
""" + remote_footer

        jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir, dry_run=False)
        print(jobid)
        if jobid != None:
            jobids.append(jobid)

## check job status

In [ ]:
stati = gt.remote.check_slurm_jobs(jobids, remote_host)

# print status for each job
completed_jobids = []
for jobid, status in zip(jobids, stati):
    print(jobid, status)
    if status in ('FAILED', 'COMPLETED', 'CANCELLED', None):
        completed_jobids.append(jobid)

# remove jobids which are completed
jobids = [jobid for jobid in jobids if jobid not in completed_jobids]

## fetch results

In [ ]:
filelist = ["*/*stiff/*/*.edr", "*/*stiff/*/dos.json", "*/*stiff/*/*.gro"]
exclude = "traj*"
gt.remote.pull_files(filelist, remote_host, remote_dir_base, exclude=exclude)

# analysis

## DoS processing functions

In [ ]:
def create_nocomp_spectra(dos_json):
    # definitions
    dos_nocomp_dict = {
        'trn': ['trn_x', 'trn_y', 'trn_z'],
        'rot': ['rot_x', 'rot_y', 'rot_z'],
        'vib': ['vib_x', 'vib_y', 'vib_z'],
        'roto': ['roto_a', 'roto_b', 'roto_c']
    }

    # sum no-component spectra from component spectra
    for h, moltype in enumerate(dos_json['moltypes']):
        # loop dos_types to build
        for dos_type_nocomp, dos_types_comp in dos_nocomp_dict.items():
            dos_nocomp_data = None
            # loop dos_types to sum
            for dos_type_comp in dos_types_comp:
                dos_comp_data = np.array(moltype['spectra'][dos_type_comp])
                if dos_nocomp_data is None:
                    dos_nocomp_data = dos_comp_data.copy()
                else:
                    dos_nocomp_data += dos_comp_data
            moltype['spectra'][dos_type_nocomp] = dos_nocomp_data

In [ ]:
def get_volume_from_npt(edr_filename):
    """returns the average volume from a gromacs .edr file"""
    with tempfile.NamedTemporaryFile(suffix='.xvg') as fp:
        run_bash(f"gmx energy -f {edr_filename} -o {fp.name} <<< 'volume'")
        data, _ = gt.xvg.load(fp.name)
    return np.mean(data['Volume'])

def get_volume_from_nvt(gro_filename):
    """returns the volume from a gromacs .gro file
    
    not working for .gro trajectories"""
    box = gt.gro.get_box(gro_filename)
    return np.prod(box)

def load_moments_of_inertia_into_moltypes(moltypes, dos_file, n_samples):
    """modifies a moltypes list, to contain moments of inertia from dos-calc"""
    with open(dos_file, 'r') as f:
        dos_json = json.load(f)
    for moltype in moltypes:
        df = pd.DataFrame(index=range(3), columns=range(n_samples))
        df.index.name = 'axis'
        df.columns.name = 'sample'
        moltype['moments_of_inertia'] = df 
        for moltype_nr, moltype in enumerate(moltypes):
            moltype['moments_of_inertia'].iloc[:] = np.array(dos_json['moltypes'][moltype_nr]['moments_of_inertia']).T

# do not use this again, seems overcomplicated
def load_doses_into_moltypes(moltypes, dos_file, n_samples, dos_names, components=False, cross=False):
    """modifies a moltypes list, to contain DoS spectra from dos-calc"""
    with open(dos_file, 'r') as f:
        dos_json = json.load(f)
    create_nocomp_spectra(dos_json)
    frequencies = dos_json['frequencies']
    
    # create data frame per moltype
    for moltype_nr, moltype in enumerate(moltypes):
        columns = pd.MultiIndex.from_arrays([['frequencies'], [0]], names=['dos', 'sample'])
        df = pd.DataFrame(columns=columns)
        df[('frequencies', 0)] = frequencies
        moltype['doses'] = df
    
    # create empty columns
    for sample in range(n_samples):
        for dos in dos_names:
            for h, moltype in enumerate(moltypes):
                if (dos['tags'] == [] 
                    or ('comp' in dos['tags'] and components)
                    or ('cross' in dos['tags'] and cross)):
                    moltype['doses'][(dos['name'], sample)] = None
    
    for moltype_nr, moltype in enumerate(moltypes):
        for dos in dos_names:
            if (dos['tags'] == [] 
                or ('comp' in dos['tags'] and components)
                or ('cross' in dos['tags'] and cross)):
                moltype['doses'].loc[:, (dos['name'], slice(None))] = np.array(dos_json['moltypes'][moltype_nr]['spectra'][dos['name']]).T

In [ ]:
def show_doses(moltypes, dos_names, additional_doses=[], components=False, cross=False, xlim=None, ylim=None, figsize=None):
    with matplotlib.rc_context(rc={'text.usetex': False}): 
        for h, moltype in enumerate(moltypes):
            frequencies = np.array(moltype['doses'][('frequencies', 0)])
            fig, ax1 = plt.subplots(figsize=figsize)
            ax1.set_title(moltype['name'])
            ax1.set_xlabel(r"wavenumber in cm¯¹")
            ax1.set_ylabel(r"DoS in kJ/mol cm")
            if xlim is not None:
                ax1.set_xlim(xlim)
            if ylim is not None:
                ax1.set_ylim(ylim)
                
            for dos in dos_names:
                if (dos['tags'] == [] 
                    or ('comp' in dos['tags'] and components)
                    or ('cross' in dos['tags'] and cross)):
                    dos_samples = np.array(moltype['doses'].loc[:, (dos['name'], slice(None))]).T
                    dos_min = dos_samples.min(axis=0)
                    dos_max = dos_samples.max(axis=0)
                    dos_mean = dos_samples.mean(axis=0)
                    line, = ax1.plot(frequencies * const.rec_cm_per_THz,
                                     dos_mean / const.rec_cm_per_THz,
                                     label=dos['name'])
                    ax1.fill_between(frequencies * const.rec_cm_per_THz,
                                     dos_min / const.rec_cm_per_THz,
                                     dos_max / const.rec_cm_per_THz,
                                     facecolor=line.get_color(), alpha=0.3)
            for i, dos in enumerate(additional_doses):
                ax1.plot(frequencies * const.rec_cm_per_THz,
                         dos / const.rec_cm_per_THz,
                         label=f'additional {i}')
            ax1.legend()
            plt.show()
            
def show_dos_integrals(moltypes, dos_names, components=False, cross=False):
    for h, moltype in enumerate(moltypes):
        frequencies = moltype['doses']['frequencies']
        for dos in dos_names:
            if (dos['tags'] == [] 
                or ('comp' in dos['tags'] and components)
                or ('cross' in dos['tags'] and cross)):
                print(dos['name'])
                print(np.trapz(moltype['doses'][dos['name']], frequencies))

## load dos

In [ ]:
for system in systems:
    print("system", system['name'])
    
    with WorkingDir(system['name']):
        load_moments_of_inertia_into_moltypes(system['moltypes'], 'dos/dos.json', param_dos['n_samples'])
        load_doses_into_moltypes(system['moltypes'], 'dos/dos.json', param_dos['n_samples'], dos_names, components=True)

## load stiff dos

In [ ]:
stiff_moltypes_dict = {}
for system in (system for system in systems if 'test_stiff' in system['tags']):
    print("system", system['name'])
        
    with WorkingDir(system['name'] + '-test-stiff'):
        stiff_moltypes = deepcopy(system['moltypes'])
        load_moments_of_inertia_into_moltypes(stiff_moltypes, 'dos/dos.json', param_dos['n_samples'])
        load_doses_into_moltypes(stiff_moltypes, 'dos/dos.json', param_dos['n_samples'], dos_names, components=True)
    stiff_moltypes_dict[system['name']] = stiff_moltypes

## generate theoretical idgas spectra

In [ ]:
def gen_spectrum_b_tre(moments_of_inertia, kB, T, n_rnd, grid_E, grid_J, frequencies, n_max):
    """generate theoretically expected TRE spectrum of rotation around intermediate axis
    
    moments of inertia large to small"""
    A = 1 / (2 * moments_of_inertia[0])
    B = 1 / (2 * moments_of_inertia[1])
    C = 1 / (2 * moments_of_inertia[2])
    J_x_sq_sps = np.random.exponential(scale=kB * T / A, size=n_rnd)
    J_y_sq_sps = np.random.exponential(scale=kB * T / B, size=n_rnd)
    J_z_sq_sps = np.random.exponential(scale=kB * T / C, size=n_rnd)

    E_sps = A*J_x_sq_sps + B*J_y_sq_sps + C*J_z_sq_sps
    J_sps = J_x_sq_sps + J_y_sq_sps + J_z_sq_sps

    hist, E_edges, J_edges = np.histogram2d(E_sps, J_sps, bins=[grid_E, grid_J], density=True)
    E_centers = (E_edges[:-1] + E_edges[1:]) / 2
    J_centers = (J_edges[:-1] + J_edges[1:]) / 2

    spectrum = np.zeros(len(frequencies))

    with np.errstate(invalid='raise'):
        for i, p_E_J_row in enumerate(hist):
            for j, p_E_J_el in enumerate(p_E_J_row):
                E = E_centers[i]
                J_sq = J_centers[j]
                if E < A*J_sq or E > C*J_sq:
                    continue
                if E - B*J_sq < 0:
                    prefactor = np.sqrt((E - A*J_sq) / (B - A))
                    omega = 2 * np.sqrt((B - A) * (C * J_sq - E))
                    m = ((C - B) * (E - A*J_sq)) / ((B - A) * (C * J_sq - E))
                if E - B*J_sq > 0:
                    prefactor = np.sqrt((E - C*J_sq) / (B - C))
                    omega = 2 * np.sqrt((B - C) * (A * J_sq - E))
                    m = ((A - B) * (E - C*J_sq)) / ((B - C) * (A * J_sq - E))
                K = scipy.special.ellipk(m)
                K_prime = scipy.special.ellipkm1(m)
                q = np.exp(-np.pi * K_prime / K)

                for n in range(n_max):
                    frequency = (2 * n + 1) * np.pi / (2 * K) * omega / (2 * np.pi)
                    magnitude = (prefactor * q**(n+1/2) / (1 - q**(2*n+1)))**2
                    magnitude *= p_E_J_el
                    peak_index = (np.abs(frequencies - frequency)).argmin()
                    spectrum[peak_index] += magnitude

        spectrum /= np.trapz(y=spectrum, x=frequencies)
        spectrum *= 1/2 * const.k_gro * T
    return spectrum, hist

In [ ]:
# this takes some time since sampling is expensive and it is not optimized

theoretical_spectra = {}
hists = {}

for system_type in system_types:
    print(system_type['name'])
    type_systems = [system for system in systems if system['type'] == system_type['name']]
    temperatures = list(set(system['temperature'] for system in type_systems))
    print('temperatures:', temperatures)

    frequencies = np.array(type_systems[0]['moltypes'][0]['doses']['frequencies'][0])
    
    moments_of_inertia = np.array(type_systems[0]['moltypes'][0]['moments_of_inertia'][0])[::-1]
    print(moments_of_inertia)

    n_bins = 1000
    n_rnd = 10**8
    n_max = 5

    for T in temperatures:
        if system_type['name'] == 'propane':
            grid_E = np.linspace(0, T / 6, n_bins)
            grid_J = np.linspace(0, T / 8, n_bins)
        else:
            grid_E = np.linspace(0, T / 10, n_bins)
            grid_J = np.linspace(0, T / 300, n_bins)
        spectrum, hist = gen_spectrum_b_tre(moments_of_inertia, const.k_gro,
                                            T, n_rnd, grid_E, grid_J, frequencies, n_max)

        fig, ax = plt.subplots(figsize=(3, 2.3))
        ax.imshow(hist, origin='lower', aspect='auto', extent=(0, max(grid_J), 0, max(grid_E)))
        plt.show()

        plt.figure(figsize=(10, 2))
        plt.plot(frequencies * const.rec_cm_per_THz, spectrum / const.rec_cm_per_THz)
        plt.xlim(0, 1000)
        plt.show()

        hists[(system_type['name'], T)] = (grid_J, grid_E, hist)
        theoretical_spectra[(system_type['name'], T)] = spectrum

In [ ]:
# save theoretical spectra and histograms
with open("theoretical-spectra.pkl", 'wb') as f:
    pickle.dump(theoretical_spectra, f)
with open("hists.pkl", 'wb') as f:
    pickle.dump(hists, f)

In [ ]:
# load theoretical spectra and histograms
with open("theoretical-spectra.pkl", 'rb') as f:
    theoretical_spectra = pickle.load(f)
with open("hists.pkl", 'rb') as f:
    hists = pickle.load(f)

## plot p(E,J) next to each other

In [ ]:
params = {
    'text.usetex' : True,
    'font.family': 'serif',
    'axes.labelsize': 10,
    'axes.titlesize': 10,
    'font.size': 10,
    'legend.fontsize': 8,
    'xtick.labelsize': 8,
    'ytick.labelsize': 8,
    'figure.dpi': 200,
}

In [ ]:
temperatures_to_show = slice(2, 3)

systems_to_show = ()

with plt.rc_context(rc=params):
    fig, axes = plt.subplots(nrows=1, ncols=2, figsize=(4.75, 1.9))
    
    for i, system_type in enumerate(system_types):
        print(system_type['name'])
        type_systems = [system for system in systems if system['type'] == system_type['name']]
        temperatures = sorted(list(set(system['temperature'] for system in type_systems)))

        frequencies = np.array(type_systems[0]['moltypes'][0]['doses']['frequencies'][0])

        moments_of_inertia = np.array(type_systems[0]['moltypes'][0]['moments_of_inertia'][0])[::-1]
        #print(moments_of_inertia)

        n_bins = 800
        for T in temperatures[temperatures_to_show]:
            print(f'T = {T}')
            grid_J, grid_E, hist = hists[(system_type['name'], T)]
        
            img = axes[i].imshow(hist, aspect='auto', origin='lower',
                                 extent=[0, max(grid_J), 0, max(grid_E)])

            axes[i].set_xlabel(r'$L^2$ in (u nm$^2$ ps$^{-1}$)$^2$')
            axes[i].set_xlim(0, max(grid_J) * 0.5)
            axes[i].set_ylim(0, max(grid_E) * 0.5)
            axes[i].set_title(system_type['name'])
            cbar = fig.colorbar(img, ax=axes[i], use_gridspec=True)
    axes[0].set_ylabel(r'$E$ in kJ mol$^{-1}$')
    
    #divider = make_axes_locatable(plt.gca())
    #cax = divider.append_axes("right", "5%", pad="3%")
    cbar.set_label(r'$p(E,L^2)$ in a.u.')

    fig.tight_layout(pad=0.2)
    #plt.subplots_adjust(left=0.1, bottom=None, right=None, top=None, wspace=None, hspace=None)
    fig.savefig(f"figures/hist-pEJ-both.pdf")
    plt.show()

In [ ]:
!cp figures/hist-*.pdf ~/research/output/dos-calc-paper/figures/

## show DoS

In [ ]:
params = {'text.usetex' : True,
          'font.family': 'serif',
          'axes.labelsize': 10,
          'font.size': 10,
          'legend.fontsize': 8,
          'xtick.labelsize': 8,
          'ytick.labelsize': 8,
          'figure.dpi': 100,
         }

In [ ]:
%matplotlib inline
xlim_dict = {'propane': (0, 100),
             'water': (0, 300)}
ylim_dict = {'propane': (0, 0.12),
             'water': (0, 0.026)}

dos_names_to_show = [dos_name for dos_name in dos_names if dos_name['name'].startswith('roto')]

for system in systems:
    print("system", system['name'])
    
    ref_system = [ref_sys for ref_sys in systems 
                  if system['name'].split('/')[0] == ref_sys['name'].split('/')[0] 
                  if 'idgas' in ref_sys['tags'] 
                  if ref_sys['temperature'] == system['temperature']][0]
    ref_moltype = ref_system['moltypes'][0]
    ref_dos_samples = np.array(ref_moltype['doses'].loc[:, ('roto_b', slice(None))]).T
    ref_dos_mean = ref_dos_samples.mean(axis=0)
    
    with plt.rc_context(rc=params):
        show_doses(system['moltypes'], dos_names_to_show,
                   #additional_doses=[theoretical_spectra[(system['type'], system['temperature'])], ref_dos_mean],
                   additional_doses=[theoretical_spectra[(system['type'], system['temperature'])]],
                   components=True, figsize=(7, 2),
                   ylim=ylim_dict[system['type']], xlim=xlim_dict[system['type']])

## show equipartition

In [ ]:
params = {'text.usetex' : False,
          'font.family': 'serif',
          'axes.labelsize': 10,
          'font.size': 10,
          'legend.fontsize': 8,
          'xtick.labelsize': 8,
          'ytick.labelsize': 8,
          'figure.dpi': 100,
         }

In [ ]:
dos_to_show = [dos for dos in dos_names if dos['name'].startswith(('roto', 'trn'))]

with plt.rc_context(rc=params):
    for system in systems:
        print("system", system['name'])
        for moltype in system['moltypes']:
            frequencies = np.array(moltype['doses'][('frequencies', 0)])
            fig, ax1 = plt.subplots(figsize=(3, 2))
                
            dos_integrals = []
            dos_integrals_err = []
            dos_integrals_dev = []
            for dos in dos_to_show:
                dos_samples = np.array(moltype['doses'].loc[:, (dos['name'], slice(None))]).T
                dos_min = dos_samples.min(axis=0)
                dos_max = dos_samples.max(axis=0)
                dos_mean = dos_samples.mean(axis=0)
                dos_integral_samples = np.trapz(x=frequencies, y=dos_samples, axis=1)
                dos_integral = dos_integral_samples.mean(axis=0) / (1/2 * const.k_gro * system['temperature'])
                dos_integral_err = dos_integral_samples.std(axis=0) / (1/2 * const.k_gro * system['temperature'])
                dos_integrals.append(dos_integral)
                dos_integrals_dev.append(dos_integral - dos['ndof'])
                dos_integrals_err.append(dos_integral_err)
            ax1.bar([dos['name'] for dos in dos_to_show], dos_integrals_dev, yerr=dos_integrals_err)
            ax1.set_ylim(-0.1, 0.1)
            ax1.set_title(moltype['name'])
            #ax1.set_ylabel(r"")
            #ax1.legend()
            plt.show()

## show multiple dos plot next to each other

In [ ]:
params = {'text.usetex' : True,
          'font.family': 'serif',
          'axes.labelsize': 10,
          'font.size': 10,
          'legend.fontsize': 8,
          'legend.labelspacing': 0.2,
          'xtick.labelsize': 8,
          'ytick.labelsize': 8,
          'figure.dpi': 150,
         }

In [ ]:
plot_params_dict = {
    'water': {'xlim': (0, 600), 'ylim': (0, 0.035)},
    'propane': {'xlim': (0, 130), 'ylim': (0, 0.085)},
}

In [ ]:
#stiff_systems_to_plot = []
stiff_systems_to_plot = names_test_stiff[0:1]
#stiff_systems_to_plot = names_test_stiff
print(stiff_systems_to_plot)

In [ ]:
plt.close('all')

T_dict = {
    'water': 832,
    'propane': 478,
}

with plt.rc_context(rc=params):
    
    fig, axes = plt.subplots(nrows=1, ncols=2, figsize=(4.75, 2.0))
    
    for i, system_type in enumerate(system_types):
        print('system type', system_type['name'])
        T = T_dict[system_type['name']]
        plot_params = plot_params_dict[system_type['name']]
        

        # plot sim idgas
        ref_system = [ref_sys for ref_sys in systems 
                      if ref_sys['type'] == system_type['name']
                      if 'idgas' in ref_sys['tags'] 
                      if ref_sys['temperature'] == T][0]
        ref_moltype = ref_system['moltypes'][0]
        frequencies = np.array(ref_moltype['doses'][('frequencies', 0)])
        ref_dos_samples = np.array(ref_moltype['doses'].loc[:, ('roto_b', slice(None))]).T
        ref_dos_min = ref_dos_samples.min(axis=0)
        ref_dos_max = ref_dos_samples.max(axis=0)
        ref_dos_mean = ref_dos_samples.mean(axis=0)

        line, = axes[i].plot(frequencies * const.rec_cm_per_THz,
                         ref_dos_mean / const.rec_cm_per_THz,
                         linestyle='-', color='gray',
                         label='sim. id. gas')
        #"""
        axes[i].fill_between(frequencies * const.rec_cm_per_THz,
                         ref_dos_min / const.rec_cm_per_THz,
                         ref_dos_max / const.rec_cm_per_THz,
                         facecolor=line.get_color(), alpha=0.3)
        #""" 

        # plot theo idgas
        theo_dos = theoretical_spectra[(ref_system['type'], T)]

        axes[i].plot(frequencies * const.rec_cm_per_THz,
                 theo_dos / const.rec_cm_per_THz,
                 linestyle='-.', color='black',
                 label='theo. id. gas')

        # print stiff
        #"""
        for stiff_system_name in stiff_systems_to_plot:
            print(stiff_system_name)
            if not stiff_system_name.startswith(system_type['name']):
                continue
            stiff_moltype = stiff_moltypes_dict[stiff_system_name][0]
            stiff_frequencies = np.array(stiff_moltype['doses'][('frequencies', 0)])
            stiff_dos_samples = np.array(stiff_moltype['doses'].loc[:, ('roto_b', slice(None))]).T
            stiff_dos_min = stiff_dos_samples.min(axis=0)
            stiff_dos_max = stiff_dos_samples.max(axis=0)
            stiff_dos_mean = stiff_dos_samples.mean(axis=0)

            line_stiff, = axes[i].plot(stiff_frequencies * const.rec_cm_per_THz,
                             stiff_dos_mean / const.rec_cm_per_THz,
                             linestyle='--', color='maroon',
                             label='sim. id. gas stiff')
        #"""

        # plot simulated systems
        systems_to_plot =  [sys for s, sys in enumerate([system for system in systems
                       if system['temperature'] == T
                       if not 'idgas' in system['tags']]) if s in [0, 3, 6, 9, 13]]
        for system in systems_to_plot:
            print("system", system['name'])

            system_type = next((st for st in system_types if st['name'] == system['type']))
            rho_c = system_type['properties']['rho_c']
            T_c = system_type['properties']['T_c']

            moltype = system['moltypes'][0]
            frequencies = np.array(moltype['doses'][('frequencies', 0)])
            dos_samples = np.array(moltype['doses'].loc[:, ('roto_b', slice(None))]).T
            dos_mean = dos_samples.mean(axis=0)

            dos_samples = np.array(moltype['doses'].loc[:, ('roto_b', slice(None))]).T
            dos_min = dos_samples.min(axis=0)
            dos_max = dos_samples.max(axis=0)
            dos_mean = dos_samples.mean(axis=0)
            line, = axes[i].plot(frequencies * const.rec_cm_per_THz,
                             dos_mean / const.rec_cm_per_THz,
                             linestyle='-',
                             label=fr"$\rho* = {system['density'] / rho_c:.3f}$")
            axes[i].fill_between(frequencies * const.rec_cm_per_THz,
                             dos_min / const.rec_cm_per_THz,
                             dos_max / const.rec_cm_per_THz,
                             facecolor=line.get_color(), alpha=0.3)

        #axes[i].set_title(moltype['name'])
        axes[i].set_xlabel(r"wavenumber in cm$^{-1}$")
        axes[i].set_xlim(plot_params['xlim'])
        axes[i].set_ylim(plot_params['ylim'])
        axes[i].set_title(system_type['name'])
    axes[0].set_ylabel(r"$S^{\mathrm{rot}\omega}_b$ in kJ/mol cm")
    axes[0].legend(frameon=False)
    legend2_elements = [line_stiff]
    axes[1].legend(handles=[line_stiff], labels=['sim. id. gas stiff'], frameon=False)
    fig.tight_layout(pad=0.1)
    fig.savefig(f"figures/dos-rotb-both.pdf")
    plt.show()

In [ ]:
!cp figures/dos-rotb-*.pdf ~/research/output/dos-calc-paper/figures/

## compare to theoretical ideal gas DoS

In [ ]:
index = [system['name'] for system in systems if not 'idgas' in system['tags']]
df_tre = pd.DataFrame(index=index)

In [ ]:
# for fitting DoS
def exponential_decay_dos(freq, lambda_, temperature):
    exp_dos = lambda_ * np.exp(-lambda_ * np.array(freq))
    return exp_dos * 1/2 * const.k_gro * temperature

def lorentz_dos(freq, lambda_, temperature):
    lorentz_dos = 2 * lambda_ / ((2 * np.pi * np.array(freq))**2 + lambda_**2)
    return lorentz_dos * 1/2 * const.k_gro * temperature

def comb_dos_exponential(p, freq, dos_tre, temperature):
    lambda_, a = p
    dos = a * dos_tre + (1-a) * exponential_decay_dos(freq, lambda_, temperature)
    return dos

def comb_dos_lorentz(p, freq, dos_tre, temperature):
    lambda_, a = p
    dos = a * dos_tre + (1-a) * lorentz_dos(freq, lambda_, temperature)
    return dos

comb_dos_used = comb_dos_exponential
#comb_dos_used = comb_dos_lorentz

def res(p, freq, dos, dos_tre, temperature):
    dos_fit = comb_dos_used(p, freq, dos_tre, temperature)
    err = dos - dos_fit
    return err

In [ ]:
for system in (system for system in systems if not 'idgas' in system['tags']):
    print("system", system['name'])
    
    # load ref
    ref_dos = theoretical_spectra[(system['type'], system['temperature'])]
    
    # load dos
    moltype = system['moltypes'][0]
    frequencies = np.array(moltype['doses'][('frequencies', 0)])
    dos_samples = np.array(moltype['doses'].loc[:, ('roto_b', slice(None))]).T
    dos_mean = dos_samples.mean(axis=0)
    
    # calc percentage using a fit of a*theo + (1-a)*exp(lambda)
    # Initial guesses for leastsq
    lambda_0, a0, = [0.5, 0.5]
    #lambda_0, a0, = [10, 0.5]
    p0 = [lambda_0, a0] 
    
    plsq = optimize.least_squares(res, p0,
                                  bounds=[[-np.inf, 0], [np.inf, 1]],
                                  args = (frequencies, dos_mean, ref_dos, system['temperature']))
    print(plsq['message'])

    #"""
    plt.figure(figsize=(5, 3))
    plt.plot(frequencies, comb_dos_used(p0, frequencies, ref_dos, system['temperature']), 'r.', label='Starting Guess')
    plt.plot(frequencies, comb_dos_used(plsq['x'], frequencies, ref_dos, system['temperature']), 'g.', label='Fitted')
    plt.plot(frequencies, dos_mean, label='Real Data')
    plt.legend()
    plt.show()
    #"""
    df_tre.at[system['name'], 'fit'] = plsq['x'][1]

In [ ]:
df_tre

## plot scatter next to each other

In [ ]:
plt.style.use('default')
params = {
    'text.usetex' : True,
    'font.family': 'serif',
    'axes.labelsize': 10,
    'font.size': 10,
    'legend.fontsize': 8,
    'legend.labelspacing': 0.1,
    'xtick.labelsize': 8,
    'ytick.labelsize': 8,
    'figure.dpi': 200,
}

In [ ]:
#metric = 'ptpm'
#cbar_label = r'$\sqrt{\int_0^\infty(DoS^{\mathrm{rot}\omega} - DoS^{\mathrm{rot}\omega}_{\mathrm{theo}})^2 \mathrm{d}f}$'
#metric = 'rmsd'
#cbar_label = r'$DoS^{\mathrm{rot}\omega}(f_\mathrm{p}) / DoS^{\mathrm{rot}\omega}_{\mathrm{theo}}(f_\mathrm{p})$'
metric = 'fit'
cbar_label = r'$\alpha$'

In [ ]:
with plt.rc_context(params):
    fig, axes = plt.subplots(nrows=1, ncols=2, figsize=(4.75, 1.9))
    for i, system_type in enumerate(system_types):
        print(system_type['name'])
        rho_c = system_type['properties']['rho_c']
        T_c = system_type['properties']['T_c']
        vap_x = np.concatenate([[rho_c], system_type['properties']['vap_liq_equi']['rho_vap']]) / rho_c
        liq_x = np.concatenate([[rho_c], system_type['properties']['vap_liq_equi']['rho_liq']]) / rho_c
        y = np.concatenate([[T_c], system_type['properties']['vap_liq_equi']['T']]) / T_c
        # plot state points
        X = []
        Y = []
        C = []
        for system in [system for system in systems if system['name'].startswith(system_type['name']) if not 'idgas' in system['tags']][::-1]:
            metric_value = df_tre.at[system['name'], metric]
            X.append(system['density'])
            Y.append(system['temperature'])
            C.append(metric_value)
        X = np.array(X) / rho_c
        Y = np.array(Y) / T_c
        # linear or logscale
        #heatmap = axes[i].scatter(X, Y, c=C, alpha=1.0, label='state point', cmap=plt.cm.viridis, vmin=0.0, vmax=1.0)
        heatmap = axes[i].scatter(X, Y, c=C, alpha=1.0, label='state point', cmap=plt.cm.viridis,
                                  norm=matplotlib.colors.LogNorm(vmin=1e-3, vmax=1.0))
        # plot binodal curves
        axes[i].plot(vap_x, y, '--k', label='binodal curve', zorder=0)
        axes[i].plot(liq_x, y, '--k', zorder=0)
        # settings
        axes[i].set_xlim(0)
        axes[i].set_ylim(0.5, 2.2)
        axes[i].set_xlabel(r"$\rho*$")
        axes[i].set_title(system_type['name'])
    # complete plot
    divider = make_axes_locatable(plt.gca())
    cax = divider.append_axes("right", "5%", pad="8%")
    cbar = plt.colorbar(heatmap, cax=cax)
    cbar.set_label(cbar_label, rotation=90)
    axes[0].legend(loc=(0.05, 0), frameon=False)
    axes[0].set_ylabel(r"$T*$")
    fig.tight_layout(pad=0.2)
    fig.savefig(f"figures/tre-{metric}-both.pdf")
    plt.show()

In [ ]:
!cp figures/tre-*.pdf ~/research/output/dos-calc-paper/figures/

## pressure and quantum vs classic

In [ ]:
# show only the four extreme cases
interesting_systems_indices = [0, 5, 67, 72, 79, 84, 147, 152]
index_tuples = [(system_type['name'], system['name'])
                for system_type in system_types
                for system in (system for system in [systems[i] for i in interesting_systems_indices]
                               if system['type'] == system_type['name'])]
index = pd.MultiIndex.from_tuples(index_tuples)
df_quantum = pd.DataFrame(index=index, columns=[])
df_quantum


In [ ]:
# trn
for system_type in system_types:
    for system in (system for system in [systems[i] for i in interesting_systems_indices]
                   if system['type'] == system_type['name']):
        #print(system_type['name'], system['name'])
        T = system['temperature']
        m = system['top'].mols()[0].mass
        de_broglie_wavelength = const.h_gro / np.sqrt(2 * np.pi * m * const.k_gro * T)
        typical_intermolecular_distance = (system['volume'] / system['top'].nmols())**(1/3)
        trn_label = r'$\frac{ \lambda_\text{th} }{ \left( \frac{V}{N} \right)^{\frac{1}{3}} }$'
        df_quantum.at[(system_type['name'], system['name']), trn_label] = de_broglie_wavelength / typical_intermolecular_distance
df_quantum

In [ ]:
# rot
for system_type in system_types:
    for system in (system for system in [systems[i] for i in interesting_systems_indices]
                   if system['type'] == system_type['name']):
        #print(system_type['name'], system['name'])
        T = system['temperature']
        I_a, I_b, I_c = system['moltypes'][0]['moments_of_inertia'][0]
        theta_a = const.hbar_gro**2 / (2 * const.k_gro * I_a)
        theta_b = const.hbar_gro**2 / (2 * const.k_gro * I_b)
        theta_c = const.hbar_gro**2 / (2 * const.k_gro * I_c)
        rot_label_a = r'$\frac{ \theta_a }{ T }$'
        rot_label_b = r'$\frac{ \theta_b }{ T }$'
        rot_label_c = r'$\frac{ \theta_c }{ T }$'
        df_quantum.at[(system_type['name'], system['name']), rot_label_a] = theta_a / T
        df_quantum.at[(system_type['name'], system['name']), rot_label_b] = theta_b / T
        df_quantum.at[(system_type['name'], system['name']), rot_label_c] = theta_c / T
df_quantum

In [ ]:
# pressure
for system_type in system_types:
    for system in (system for system in [systems[i] for i in interesting_systems_indices]
                   if system['type'] == system_type['name']):
        #print(system_type['name'], system['name'])
        with WorkingDir(system['name']):
            run_bash("gmx energy -f prod/ener.edr -o energy-temp.xvg <<< 'pressure'")
            xvg_pressure, _ = gt.xvg.load('energy-temp.xvg')
            run_bash("rm energy-temp.xvg")
        pressure = xvg_pressure['Pressure'].mean()
        df_quantum.at[(system_type['name'], system['name']), r'$\frac{p}{\mathrm{bar}}$'] = pressure
df_quantum

In [ ]:
# relabel
index_tuples = [(system_type['name'],
                 f"$\rho* = {system['density'] / system_type['properties']['rho_c']:.2f}$, "
                 f"$T* = {system['temperature'] / system_type['properties']['T_c']:.2f}$")
                for system_type in system_types
                for system in (system for system in [systems[i] for i in interesting_systems_indices]
                               if system['type'] == system_type['name'])]
index = pd.MultiIndex.from_tuples(index_tuples)
df_quantum.index = index
df_quantum

In [ ]:
with open('figures/tre-quantum.tex', 'w') as f:
    df_quantum.to_latex(f, escape=False, formatters=["{:0.4f}".format]*4 + ["{:.1f}".format])
!cat figures/tre-quantum.tex

In [ ]:
!cp figures/tre-quantum.tex ~/research/output/dos-calc-paper/figures/tre-quantum.tex

In [ ]:
# test hydrogen
I_a = 2 * 1.008 * (0.109 / 2)**2  # u * nm²
print(I_a)
print(const.hbar_gro**2 / (2 * const.k_gro * I_a))

# molecule inspection

## some functions

In [ ]:
def set_axes_radius(ax, origin, radius):
    ax.set_xlim3d([origin[0] - radius, origin[0] + radius])
    ax.set_ylim3d([origin[1] - radius, origin[1] + radius])
    ax.set_zlim3d([origin[2] - radius, origin[2] + radius])

    
def set_axes_equal(ax):
    '''Make axes of 3D plot have equal scale so that spheres appear as spheres,
    cubes as cubes, etc..  This is one possible solution to Matplotlib's
    ax.set_aspect('equal') and ax.axis('equal') not working for 3D.

    Input
      ax: a matplotlib axis, e.g., as output from plt.gca().
    '''

    limits = np.array([
        ax.get_xlim3d(),
        ax.get_ylim3d(),
        ax.get_zlim3d(),
    ])

    origin = np.mean(limits, axis=1)
    radius = 0.5 * np.max(np.abs(limits[:, 1] - limits[:, 0]))
    set_axes_radius(ax, origin, radius)
    
    
def add_sphere_to_ax(axis, radius, pos, color, res_u=20, res_v=10, linewidth=0.1):
    u, v = np.mgrid[0:2*np.pi:res_u*1j, 0:np.pi:res_v*1j]
    x = radius * np.cos(u)*np.sin(v) + pos[0]
    y = radius * np.sin(u)*np.sin(v) + pos[1]
    z = radius * np.cos(v) + pos[2]
    axis.plot_wireframe(x, y, z, color=color, linewidth=linewidth)

In [ ]:
systems_to_show = systems[-1:]
gro_files_molecules_to_show = [('prod/confout.gro', [0])]
show_plot = True

In [ ]:
%matplotlib widget

# assumes the single.gro files are energy minimized
for system in systems_to_show:
    print(system['name'])
    for gro_file, molecules in gro_files_molecules_to_show:
        print(gro_file)
        for molecule in molecules:
            print(molecule, end=' ')

            # load structure
            top = deepcopy(system['top'])
            with WorkingDir(system['name']):
                top.load_gro_file_pos_vel(gro_file)
            mol = top.mols()[molecule]
            del top

            # load into simple format
            masses = np.array([atom.mass for atom in mol.atoms()])
            names = np.array([atom.name for atom in mol.atoms()])
            positions = np.array([atom.pos for atom in mol.atoms()])
            natoms = len(masses)
            center_of_mass = np.dot(masses, positions) / mol.mass
            positions_relative = positions - center_of_mass
            
            # calc abc vectors
            def get_pos_for_abc(indicator, positions_relative):
                if indicator == -1:
                    return np.zeros(3)
                else:
                    return positions_relative[indicator]
            abc_ind = system['moltypes'][0]['abc_indicators']
            a = get_pos_for_abc(abc_ind[0], positions_relative) - get_pos_for_abc(abc_ind[1], positions_relative)
            b_prime = get_pos_for_abc(abc_ind[2], positions_relative) - get_pos_for_abc(abc_ind[3], positions_relative)
            c = np.cross(a, b_prime)
            b = np.cross(c, a)
            a, b, b_prime, c = map(lambda x: x / np.linalg.norm(x), [a, b, b_prime, c])
            
            # calculate principal axes
            moment_of_inertia_tensor = np.zeros([3, 3])
            for atom in range(len(masses)):
                p_ = positions_relative[atom]
                moment_of_inertia_tensor += masses[atom] * ((p_ @ p_) * np.identity(3) - p_[:, np.newaxis] @ p_[np.newaxis, :])
            values, vectors = np.linalg.eig(moment_of_inertia_tensor)
            idx = values.argsort()[::1]   
            values = values[idx]
            vectors = vectors[:,idx]
            
            # show parallel a and vector[0], ...
            print(np.allclose(np.abs([vectors.T[0] @ a, vectors.T[1] @ b, vectors.T[2] @ c]), np.ones(3)), end=' ')

            if show_plot:
                # initialize plot
                fig = plt.figure(figsize=(6, 6))
                ax = fig.add_subplot(111, projection='3d', proj_type='persp')

                # plot atoms
                for j in range(natoms):
                    add_sphere_to_ax(ax, 0.01, positions_relative[j], 'g')
                    ax.text(*positions_relative[j], names[j], None)

                # plot com
                add_sphere_to_ax(ax, 0.01, [0, 0, 0], 'b')
                ax.text(0, 0, 0, 'COM', None)

                # plot abc vectors
                ax.quiver(0, 0, 0, *a, length=0.1)
                ax.quiver(0, 0, 0, *b, length=0.1)
                #ax.quiver(0, 0, 0, *b_prime, length=0.1)
                ax.quiver(0, 0, 0, *c, length=0.1)
                ax.text(*0.1*a, 'a', None)
                ax.text(*0.1*b, 'b', None)
                #ax.text(*0.1*b_prime, "b'", None)
                ax.text(*0.1*c, 'c', None)

                # plot principal axes
                for i, vector in enumerate(vectors.T):
                    ax.quiver(0, 0, 0, *vector, length=0.1)
                    ax.text(*0.1*vector, f"{i} {values[i]:.2f}", None, verticalalignment='top')

                # plot
                ax.set_xlabel('X axis')
                ax.set_ylabel('Y axis')
                ax.set_zlabel('Z axis')
                set_axes_equal(ax)
                plt.show()

## archive

### alternative sprectra generation

In [ ]:
def gen_spectra_tre(moments_of_inertia, kB, T, n_rnd, grid_E, grid_J, frequencies, n_max):
    """generate theoretically expected TRE spectrum of rotation around all axes
    
    moments of inertia large to small"""
    A = 1 / (2 * moments_of_inertia[0])
    B = 1 / (2 * moments_of_inertia[1])
    C = 1 / (2 * moments_of_inertia[2])
    J_x_sq_sps = np.random.exponential(scale=kB * T / A, size=n_rnd)
    J_y_sq_sps = np.random.exponential(scale=kB * T / B, size=n_rnd)
    J_z_sq_sps = np.random.exponential(scale=kB * T / C, size=n_rnd)

    E_sps = A*J_x_sq_sps + B*J_y_sq_sps + C*J_z_sq_sps
    J_sps = J_x_sq_sps + J_y_sq_sps + J_z_sq_sps

    hist, E_edges, J_edges = np.histogram2d(E_sps, J_sps, bins=[grid_E, grid_J])
    E_centers = (E_edges[:-1] + E_edges[1:]) / 2
    J_centers = (J_edges[:-1] + J_edges[1:]) / 2

    spectrum_a = np.zeros(len(frequencies))
    spectrum_b = np.zeros(len(frequencies))
    spectrum_c = np.zeros(len(frequencies))

    with np.errstate(invalid='raise'):
        for i, p_E_J_row in enumerate(hist):
            for j, p_E_J_el in enumerate(p_E_J_row):
                E = E_centers[i]
                J_sq = J_centers[j]
                if E < A*J_sq or E > C*J_sq:
                    continue
                if E - B*J_sq < 0:
                    prefactor_a = np.sqrt((E - C*J_sq) / (A - C))
                    prefactor_b = np.sqrt((E - A*J_sq) / (B - A))
                    prefactor_c = np.sqrt((E - A*J_sq) / (C - A))
                    omega = 2 * np.sqrt((B - A) * (C * J_sq - E))
                    m = ((C - B) * (E - A*J_sq)) / ((B - A) * (C * J_sq - E))
                elif E - B*J_sq > 0:
                    prefactor_a = np.sqrt((E - C*J_sq) / (A - C))
                    prefactor_b = np.sqrt((E - C*J_sq) / (B - C))
                    prefactor_c = np.sqrt((E - A*J_sq) / (C - A))
                    omega = 2 * np.sqrt((B - C) * (A * J_sq - E))
                    m = ((A - B) * (E - C*J_sq)) / ((B - C) * (A * J_sq - E))
                K = scipy.special.ellipk(m)
                K_prime = scipy.special.ellipkm1(m)
                q = np.exp(-np.pi * K_prime / K)

                for n in range(n_max):
                    frequency_sn_cn = ((2 * n) + 1) * np.pi / (2 * K) * omega / (2 * np.pi)
                    frequency_dn = 2 * n * np.pi / (2 * K) * omega / (2 * np.pi)
                    magnitude_b = (prefactor_b * q**(n+1/2) / (1 - q**(2*n+1)))**2
                    if E - B*J_sq < 0:
                        magnitude_a = (prefactor_a * q**n / (1 + q**(2*n)))**2
                        magnitude_c = (prefactor_c * q**(n+1/2) / (1 + q**(2*n+1)))**2
                    elif E - B*J_sq > 0:
                        magnitude_a = (prefactor_a * q**(n+1/2) / (1 + q**(2*n+1)))**2
                        magnitude_c = (prefactor_c * q**n / (1 + q**(2*n)))**2
                    magnitude_a *= p_E_J_el
                    magnitude_b *= p_E_J_el
                    magnitude_c *= p_E_J_el
                    peak_index_sn_cn = (np.abs(frequencies - frequency_sn_cn)).argmin()
                    peak_index_dn = (np.abs(frequencies - frequency_dn)).argmin()
                    spectrum_b[peak_index_sn_cn] += magnitude_b
                    if E - B*J_sq < 0:
                        spectrum_a[peak_index_dn] += magnitude_a
                        spectrum_c[peak_index_sn_cn] += magnitude_c
                    elif E - B*J_sq > 0:
                        spectrum_a[peak_index_sn_cn] += magnitude_a
                        spectrum_c[peak_index_dn] += magnitude_c

        for spectrum in (spectrum_a, spectrum_b, spectrum_c):
            spectrum /= np.trapz(y=spectrum, x=frequencies)
            spectrum *= 1/2 * const.k_gro * T
    return spectrum_a, spectrum_b, spectrum_c, hist

In [ ]:
def gen_spectra_tre_new(moments_of_inertia, kB, T, n_rnd, grid_E, grid_J, frequencies, n_max):
    """generate theoretically expected TRE spectrum of rotation around all axes
    
    alternative method with uniform sampling of the angular momenta. Sampling is worse.
    
    moments of inertia large to small"""
    A = 1 / (2 * moments_of_inertia[0])
    B = 1 / (2 * moments_of_inertia[1])
    C = 1 / (2 * moments_of_inertia[2])
    J_x_sq_sps = np.random.uniform(low=0.0, high=max(grid_J), size=n_rnd)
    J_y_sq_sps = np.random.uniform(low=0.0, high=max(grid_J), size=n_rnd)
    J_z_sq_sps = np.random.uniform(low=0.0, high=max(grid_J), size=n_rnd)

    E_sps = A*J_x_sq_sps + B*J_y_sq_sps + C*J_z_sq_sps
    J_sps = J_x_sq_sps + J_y_sq_sps + J_z_sq_sps

    hist, E_edges, J_edges = np.histogram2d(E_sps, J_sps, bins=[grid_E, grid_J], weights=np.exp(-E_sps/const.k_gro/T))
    E_centers = (E_edges[:-1] + E_edges[1:]) / 2
    J_centers = (J_edges[:-1] + J_edges[1:]) / 2

    spectrum_a = np.zeros(len(frequencies))
    spectrum_b = np.zeros(len(frequencies))
    spectrum_c = np.zeros(len(frequencies))

    with np.errstate(invalid='raise'):
        for i, p_E_J_row in enumerate(hist):
            for j, p_E_J_el in enumerate(p_E_J_row):
                E = E_centers[i]
                J_sq = J_centers[j]
                if E < A*J_sq or E > C*J_sq:
                    continue
                if E - B*J_sq < 0:
                    prefactor_a = np.sqrt((E - C*J_sq) / (A - C))
                    prefactor_b = np.sqrt((E - A*J_sq) / (B - A))
                    prefactor_c = np.sqrt((E - A*J_sq) / (C - A))
                    omega = 2 * np.sqrt((B - A) * (C * J_sq - E))
                    m = ((C - B) * (E - A*J_sq)) / ((B - A) * (C * J_sq - E))
                elif E - B*J_sq > 0:
                    prefactor_a = np.sqrt((E - C*J_sq) / (A - C))
                    prefactor_b = np.sqrt((E - C*J_sq) / (B - C))
                    prefactor_c = np.sqrt((E - A*J_sq) / (C - A))
                    omega = 2 * np.sqrt((B - C) * (A * J_sq - E))
                    m = ((A - B) * (E - C*J_sq)) / ((B - C) * (A * J_sq - E))
                K = scipy.special.ellipk(m)
                K_prime = scipy.special.ellipkm1(m)
                q = np.exp(-np.pi * K_prime / K)

                for n in range(n_max):
                    frequency_sn_cn = ((2 * n) + 1) * np.pi / (2 * K) * omega / (2 * np.pi)
                    frequency_dn = 2 * n * np.pi / (2 * K) * omega / (2 * np.pi)
                    magnitude_b = (prefactor_b * q**(n+1/2) / (1 - q**(2*n+1)))**2
                    if E - B*J_sq < 0:
                        magnitude_a = (prefactor_a * q**n / (1 + q**(2*n)))**2
                        magnitude_c = (prefactor_c * q**(n+1/2) / (1 + q**(2*n+1)))**2
                    elif E - B*J_sq > 0:
                        magnitude_a = (prefactor_a * q**(n+1/2) / (1 + q**(2*n+1)))**2
                        magnitude_c = (prefactor_c * q**n / (1 + q**(2*n)))**2
                    magnitude_a *= p_E_J_el
                    magnitude_b *= p_E_J_el
                    magnitude_c *= p_E_J_el
                    peak_index_sn_cn = (np.abs(frequencies - frequency_sn_cn)).argmin()
                    peak_index_dn = (np.abs(frequencies - frequency_dn)).argmin()
                    spectrum_b[peak_index_sn_cn] += magnitude_b
                    if E - B*J_sq < 0:
                        spectrum_a[peak_index_dn] += magnitude_a
                        spectrum_c[peak_index_sn_cn] += magnitude_c
                    elif E - B*J_sq > 0:
                        spectrum_a[peak_index_sn_cn] += magnitude_a
                        spectrum_c[peak_index_dn] += magnitude_c

        for spectrum in (spectrum_a, spectrum_b, spectrum_c):
            spectrum /= np.trapz(y=spectrum, x=frequencies)
            spectrum *= 1/2 * const.k_gro * T
    return spectrum_a, spectrum_b, spectrum_c, hist

### single theoretical spectrum 

In [ ]:

# weird water
#moments_of_inertia = np.array([0.008247, 0.009186, 0.017432])[::-1]
#T = 832
#grid_E = np.linspace(0, T / 10, n_bins)
#grid_J = np.linspace(0, T / 400, n_bins)

# water
#moments_of_inertia = np.array([0.006146, 0.011551, 0.017696])[::-1]
#T = 832
#grid_E = np.linspace(0, T / 10, n_bins)
#grid_J = np.linspace(0, T / 400, n_bins)

# propane
moments_of_inertia = np.array([0.070686, 0.481466, 0.552152])[::-1]
T = 512
n_bins = 300
grid_E = np.linspace(0, T / 8, n_bins)
grid_J = np.linspace(0, T / 10, n_bins)

n_rnd = int(1e6)
n_max = 5
frequencies = np.linspace(0, 20, 200)

In [ ]:
spectrum_a, spectrum_b, spectrum_c, hist = gen_spectra_tre(moments_of_inertia, const.k_gro,
                                                           T, n_rnd, grid_E, grid_J, frequencies, n_max)

In [ ]:
spectrum_a_new, spectrum_b_new, spectrum_c_new, hist_new = gen_spectra_tre_new(moments_of_inertia, const.k_gro,
                                                                               T, n_rnd, grid_E, grid_J, frequencies, n_max)

In [ ]:
plt.style.use('seaborn-muted')
params = {
    #'text.usetex' : True,
    'font.family': 'serif',
    'axes.labelsize': 10,
    'font.size': 10,
    'legend.fontsize': 8,
    'xtick.labelsize': 8,
    'ytick.labelsize': 8,
    'figure.dpi': 200,
         }
plt.rcParams.update(params) 

In [ ]:
for hist_ in [hist, hist_new]:
    fig, ax = plt.subplots(figsize=(3, 2.3))
    img = ax.imshow(hist_, aspect='auto', origin='lower',
                    extent=[0, max(grid_J), 0, max(grid_E)])

    ax.set_xlabel(r'$J$ in u nm$^2$ ps$^{-1}$')
    ax.set_ylabel(r'$E$ in kJ mol$^{-1}$')
    #ax.set_xlim(0, max(grid_J) * 1.0)
    #ax.set_ylim(0, max(grid_E) * 1.0)
    cbar = fig.colorbar(img, ax=ax)
    cbar.set_label(r'$p(E,J)$ in a.u.')
    fig.tight_layout()
    #fig.savefig(f"figures/hist-pEJ-{system_type['name']}.pdf")
    plt.show()

plt.figure(figsize=(10, 2))
plt.plot(frequencies, spectrum_a, label='a')
plt.plot(frequencies, spectrum_b, label='b')
plt.plot(frequencies, spectrum_c, label='c')
plt.plot(frequencies, spectrum_a_new, label='a new')
plt.plot(frequencies, spectrum_b_new, label='b new')
plt.plot(frequencies, spectrum_c_new, label='c new')
plt.legend()
plt.xlim(0, 10)
plt.ylim(0, 3.2)
plt.show()

## show moments of inertia

In [ ]:
print(systems[0]['moltypes'][0]['moments_of_inertia'][0])
print(systems[-1]['moltypes'][0]['moments_of_inertia'][0])
print(list(stiff_moltypes_dict.values())[0][0]['moments_of_inertia'][0])

# thermostat test data generation

## prepare test thermostat

In [ ]:
for system in (system for system in systems if 'test_thermostat' in system['tags']):
    print(f"system {system['name']}")
    
    for thermostat_dict in thermostats_to_test:
        thermostat_name = thermostat_dict['name']
        thermostat_key = thermostat_dict['key']
        tau_t = thermostat_dict['tau-t']
        print('  ' + thermostat_name)
          
        with WorkingDir(system['name'] + '-test-thermostat/' + thermostat_name):
            # make dirs and copy template files
            run_bash("mkdir -p equi1 equi2 prod topol dos")
            system_type = system['type']
            run_bash(f"cp -Tr {template_dir}/{system_type}/topol topol")
            run_bash(f"cp {template_dir}/{system_type}/tt/{thermostat_key}/equi1.mdp equi1/grompp.mdp")
            run_bash(f"cp {template_dir}/{system_type}/tt/{thermostat_key}/equi2.mdp equi2/grompp.mdp")
            run_bash(f"cp {template_dir}/{system_type}/tt/{thermostat_key}/prod.mdp prod/grompp.mdp")
            
            # run length
            gt.mdp.set_parameter("equi1/grompp.mdp", 'nsteps',  10000)
            gt.mdp.set_parameter("equi2/grompp.mdp", 'nsteps', 200000)
            gt.mdp.set_parameter("prod/grompp.mdp", 'nsteps',  200000)

            # set temperature
            gt.mdp.set_parameter("equi2/grompp.mdp", 'gen-temp', system['temperature'])
            gt.mdp.set_parameter("equi2/grompp.mdp", 'ref-t', system['temperature'])
            if not thermostat_key == 'no':
                gt.mdp.set_parameter("prod/grompp.mdp", 'ref-t',  system['temperature'])
            
            # set tau-t
            if thermostat_key == 'no':
                gt.mdp.set_parameter("equi2/grompp.mdp", 'tau-t', 20)
            else:
                gt.mdp.set_parameter("equi2/grompp.mdp", 'tau-t', tau_t)
            if not thermostat_key == 'no':
                gt.mdp.set_parameter("prod/grompp.mdp", 'tau-t', tau_t)

            # copy dos-params
            run_bash(f"cp ../../../{system['name']}/dos/params.json dos/params.json")
            
            # copy conf.gro
            run_bash(f"cp ../../../{system['name']}/equi1/conf.gro equi1/conf.gro")

## thermostat test md on cluster

In [ ]:
for system in (system for system in systems if 'test_thermostat' in system['tags']):
    print(f"system {system['name']}")
    
    for thermostat_dict in thermostats_to_test:
        thermostat_name = thermostat_dict['name']
        thermostat_key = thermostat_dict['key']
        tau_t = thermostat_dict['tau-t']
        print('  ' + thermostat_name)
          
        remote_dir = os.path.join(remote_dir_base, system['name'] + '-test-thermostat/' + thermostat_name)
        with WorkingDir(system['name'] + '-test-thermostat/' + thermostat_name):
            
            # mkdir
            run_bash(f"ssh {remote_host} mkdir -p {remote_dir}")

            # copy simulation files to remote
            filelist = ["topol",
                        "equi1/conf.gro",
                        "equi1/grompp.mdp",
                        "equi2/grompp.mdp",
                        "prod/grompp.mdp",
                        "dos/params.json"]
            gt.remote.push_files(filelist, remote_host, remote_dir, exclude="traj*")

            # commands to be run on compute nodes
            temperature = system['temperature']
            script = remote_header + f"""
pushd equi1
    if [[ ! -f confout.gro ]]
        then
        gmx grompp -p ../topol/topol.top
        gmx mdrun
    fi
    rm -f \#*
popd

pushd equi2
    if [[ ! -f confout.gro ]]
        then
        gmx grompp -p ../topol/topol.top -c ../equi1/confout.gro -maxwarn 1
        gmx mdrun
    fi
    rm -f \#*
popd

if [[ ! -f dos/dos.json ]]
then
    pushd prod
        gmx grompp -p ../topol/topol.top -c ../equi2/confout.gro -maxwarn 1
        gmx mdrun -o $JOBTMP/traj.trr
        ls -lh $JOBTMP/
        rm -f \#*
    popd

    pushd dos
        dos-calc -v params.json $JOBTMP/traj.trr
        rm -f \#*
    popd
fi
"""

            jobid = gt.remote.run_slurm_script(script, remote_host, remote_dir, dry_run=False)
            print(jobid)
            if jobid != None:
                jobids.append(jobid)

## check job status

In [ ]:
stati = gt.remote.check_slurm_jobs(jobids, remote_host)

# print status for each job
completed_jobids = []
for jobid, status in zip(jobids, stati):
    print(jobid, status)
    if status in ('FAILED', 'COMPLETED', 'CANCELLED', None):
        completed_jobids.append(jobid)

# remove jobids which are completed
jobids = [jobid for jobid in jobids if jobid not in completed_jobids]

## fetch results

In [ ]:
filelist = ["**/*.edr", "**/dos.json", "**/*.gro"]
exclude = "traj*"
gt.remote.pull_files(filelist, remote_host, remote_dir_base, exclude=exclude)

## equilibration check

In [ ]:
def show_energy_graphs(properties_list, edr_file="ener.edr"):
    run_bash("gmx energy -f {} -o energy-temp.xvg <<< '{}'".format(edr_file, "\n".join(properties_list)))
    gt.xvg.plot("energy-temp.xvg")
    run_bash("rm energy-temp.xvg")

In [ ]:
for system in (system for system in systems if 'test_thermostat' in system['tags']):
    print(f"system {system['name']}")
    
    for thermostat_dict in thermostats_to_test:
        thermostat_name = thermostat_dict['name']
        print('  ' + thermostat_name)
          
        with WorkingDir(system['name'] + '-test-thermostat/' + thermostat_name):
            #print("equilibration 1")
            #show_energy_graphs(["Temperature"], edr_file="equi1/ener.edr")
            #show_energy_graphs(["Pressure"], edr_file="equi1/ener.edr")
            #print("equilibration 2")
            #show_energy_graphs(["Temperature"], edr_file="equi2/ener.edr")
            #show_energy_graphs(["Pressure"], edr_file="equi2/ener.edr")
            print("production")
            show_energy_graphs(["Temperature"], edr_file="prod/ener.edr")
            #show_energy_graphs(["Pressure"], edr_file="prod/ener.edr")

# thermostat test analysis

## load dos

In [ ]:
systems_thermostats_dict = {}
for system in (system for system in systems if 'test_thermostat' in system['tags']):
    print(f"system {system['name']}")
    
    for thermostat_dict in thermostats_to_test:
        thermostat_name = thermostat_dict['name']
        print('  ' + thermostat_name)
        
        moltypes = deepcopy(system['moltypes'])
        for moltype in moltypes:
            moltype['doses'] = None
          
        with WorkingDir(system['name'] + '-test-thermostat/' + thermostat_name):
            load_doses_into_moltypes(moltypes, 'dos/dos.json', param_dos['n_samples'], dos_names, components=True)
        systems_thermostats_dict[(system['name'], thermostat_name)] = {'moltypes': moltypes, 'refsys': system}

## show multiple dos plot

In [ ]:
thermostats_to_test

In [ ]:
thermostats_to_show = thermostats_to_test[2:10:2] + thermostats_to_test[9:12:1] + thermostats_to_test[0:1]
plot_params_dict = {
    'water': {'xlim': (0, 320), 'ylim': (0, 0.03)},
    'propane': {'xlim': (0, 90), 'ylim': (0, 0.062)},
}
plot_params2_dict = {
    'no': {'linestyle': '-', 'color': 'k'},
    'andersen-massive': {'linestyle': ':', 'color': None},
    'v-rescale': {'linestyle': '-.', 'color': None},
    'sd': {'linestyle': '--', 'color': None},
}
thermostat_shortnames_dict = {
    'no': 'None',
    'sd': 'SD',
    'v-rescale': 'VR',
    'andersen-massive': 'AM',
}

In [ ]:
plt.style.use('seaborn-muted')
params = {
    #'text.usetex' : True,
    'font.family': 'serif',
    'axes.labelsize': 8,
    'font.size': 8,
    'legend.fontsize': 6,
    'xtick.labelsize': 8,
    'ytick.labelsize': 8,
    'figure.dpi': 200,
}

In [ ]:
plt.close('all')

with plt.rc_context(rc=params):
    systems_thermostats_list = []
    for system in (system for system in systems if 'test_thermostat' in system['tags']):
        print(f"system {system['name']}")
        plot_params = plot_params_dict[system['type']]

        fig, ax1 = plt.subplots(figsize=(3, 2.1))
        #fig, ax1 = plt.subplots(figsize=(5, 3))

        for thermostat_dict in thermostats_to_show:
            thermostat_name = thermostat_dict['name']
            thermostat_key = thermostat_dict['key']
            tau_t = thermostat_dict['tau-t']
            thermostat_shortname = thermostat_shortnames_dict[thermostat_key]
            print('  ' + thermostat_name)
            try:
                moltypes = systems_thermostats_dict[(system['name'], thermostat_name)]['moltypes']
            except:
                print('skipping:', system['name'], thermostat_name)
                continue


            for moltype in moltypes:
                plot_params2 = plot_params2_dict[thermostat_key]
                frequencies = np.array(moltype['doses'][('frequencies', 0)])
                dos_samples = np.array(moltype['doses'].loc[:, ('roto_b', slice(None))]).T
                dos_min = dos_samples.min(axis=0)
                dos_max = dos_samples.max(axis=0)
                dos_mean = dos_samples.mean(axis=0)
                if thermostat_name == 'no':
                    label = "NVE"
                else:
                    label = fr"{thermostat_shortname}, $\tau = {tau_t}$ ps"
                line, = ax1.plot(frequencies * const.rec_cm_per_THz,
                                 dos_mean / const.rec_cm_per_THz,
                                 linestyle=plot_params2['linestyle'],
                                 color=plot_params2['color'],
                                 label=label)
                #"""
                ax1.fill_between(frequencies * const.rec_cm_per_THz,
                                 dos_min / const.rec_cm_per_THz,
                                 dos_max / const.rec_cm_per_THz,
                                 facecolor=line.get_color(), alpha=0.1)
                #"""

        #ax1.set_title(moltype['name'])
        ax1.set_xlabel(r"wavenumber in cm¯¹")
        ax1.set_ylabel(r"$S^{\mathrm{rot}\omega}_b$ in kJ/mol cm")
        ax1.set_xlim(plot_params['xlim'])
        ax1.set_ylim(plot_params['ylim'])
        ax1.legend()
        fig.tight_layout(pad=0.2)
        fig.savefig(f"figures/dos-rotb-{system['type']}-thermostats.pdf")
        plt.show()


In [ ]:
IFrame(f"figures/dos-rotb-{system['type']}-thermostats.pdf", width=600, height=340)

In [ ]:
!cp figures/dos-rotb-*-thermostats.pdf ~/research/output/dos-calc-paper/figures/

In [ ]:
def show_energy_graphs(properties_list, edr_file="ener.edr"):
    run_bash("gmx energy -f {} -o energy-temp.xvg <<< '{}'".format(edr_file, "\n".join(properties_list)))
    gt.xvg.plot("energy-temp.xvg")
    run_bash("rm energy-temp.xvg")

In [ ]:
for system in (system for system in systems if 'test_stiff' in system['tags']):
    print(f"system {system['name']}")
    
    with WorkingDir(system['name'] + '-test-stiff'):
        print("equilibration 1")
        show_energy_graphs(["Temperature"], edr_file="equi1/ener.edr")
        show_energy_graphs(["Pressure"], edr_file="equi1/ener.edr")
        print("equilibration 2")
        show_energy_graphs(["Temperature"], edr_file="equi2/ener.edr")
        show_energy_graphs(["Pressure"], edr_file="equi2/ener.edr")
        print("production")
        show_energy_graphs(["Temperature"], edr_file="prod/ener.edr")
        show_energy_graphs(["Pressure"], edr_file="prod/ener.edr")

In [ ]:
plt.plot(np.loadtxt('/tmp/temp'), '.-')
plt.xlim(0, 10)
#plt.xlim(990, 1010)
plt.show()